# Set up Colab

In [2]:
%pip install -qU torchinfo python-dotenv pytorch-ignite

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 312.7/312.7 kB 19.2 MB/s eta 0:00:00


In [3]:
from google.colab import drive

drive.mount("/content/drive")

Mounted at /content/drive


In [31]:
# Add src module
import sys

sys.path.insert(
    0, str("/content/drive/MyDrive/AI Talent Hub/Обработка и генерация изображений/images_hw_3")
)
print(sys.path)

['/content/drive/MyDrive/AI Talent Hub/Обработка и генерация изображений/images_hw_3', '/content/drive/MyDrive/AI Talent Hub/Обработка и генерация изображений/images_hw_3', '/content/drive/MyDrive/AI Talent Hub/Обработка и генерация изображений/images_hw_3', '/content', '/env/python', '/usr/lib/python311.zip', '/usr/lib/python3.11', '/usr/lib/python3.11/lib-dynload', '', '/usr/local/lib/python3.11/dist-packages', '/usr/lib/python3/dist-packages', '/usr/local/lib/python3.11/dist-packages/IPython/extensions', '/usr/local/lib/python3.11/dist-packages/setuptools/_vendor', '/root/.ipython', '/tmp/tmpmvw4d7px']


# Set up notebook

In [32]:
%load_ext autoreload
%autoreload 2

The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload


In [33]:
import random
from multiprocessing import cpu_count
from pathlib import Path

import numpy as np
import torch
import torch.nn as nn
import torchvision
import torchvision.transforms.v2 as transforms
import wandb
from torch.utils.data import DataLoader, Subset
from torchvision.models import resnet18

from src.metrics import Metrics
from src.pipeline import logits_distillation_train, untrained_hidden_layer_distillation_train, test, hybrid_distillation_train
from src.utils import Identity

In [7]:
# Supress torch dynamo warnings
import torch._dynamo

torch._dynamo.config.suppress_errors = True

In [8]:
# Load wandb key

# Local
# load_dotenv()

# Colab
from google.colab import userdata

WANDB_KEY = userdata.get("WANDB_KEY")

In [9]:
# Ensure deterministic behavior
from numpy.random import MT19937, RandomState, SeedSequence

random.seed(3)
rs = RandomState(MT19937(SeedSequence(3)))
torch.backends.cudnn.deterministic = True
torch.manual_seed(3)
torch.cuda.manual_seed_all(3)

In [10]:
# Device configuration
device = torch.device("cuda:0" if torch.cuda.is_available() else "cpu")
device

device(type='cuda', index=0)

# Set up data

In [11]:
transform = transforms.Compose(
    [
        transforms.ToImage(),
        transforms.ToDtype(torch.float32, scale=True),
        transforms.Normalize((0.5, 0.5, 0.5), (0.5, 0.5, 0.5)),
    ]
)

batch_size = 512

classes = ("plane", "car", "bird", "cat", "deer", "dog", "frog", "horse", "ship", "truck")
i2c = {i: c for i, c in enumerate(classes)}

trainset = torchvision.datasets.CIFAR10(
    root="./data", train=True, download=True, transform=transform
)
testset = torchvision.datasets.CIFAR10(
    root="./data", train=False, download=True, transform=transform
)

100%|██████████| 170M/170M [00:12<00:00, 13.3MB/s]


Extracting ./data/cifar-10-python.tar.gz to ./data
Files already downloaded and verified


In [12]:
# Make validation set
valset_ids = rs.choice(len(trainset), 5000, False)
valset = Subset(trainset, valset_ids)

trainset = Subset(trainset, np.delete(np.arange(len(trainset)), valset_ids))

In [13]:
[len(d) for d in (trainset, valset, testset)]

[45000, 5000, 10000]

In [14]:
trainloader = DataLoader(trainset, batch_size=batch_size, shuffle=True, num_workers=cpu_count())
valloader = DataLoader(valset, batch_size=batch_size, shuffle=False, num_workers=cpu_count())
testloader = DataLoader(testset, batch_size=batch_size, shuffle=False, num_workers=cpu_count())

# Experiment 1: logits distillation

## Load models

In [ ]:
# Load pretrained teacher model
teacher = torch.load("/content/resnet18_14_15_14.pt", map_location=device)
teacher = torch.compile(teacher)

# Set up student model
student = resnet18()
student.conv1 = nn.Conv2d(3, 64, kernel_size=3, stride=1, padding=1, bias=False)
student.maxpool = Identity()
student.layer1[1] = Identity()
student.layer2[1] = Identity()
student.layer3[1] = Identity()
student.layer4 = Identity()
student.fc = nn.Linear(256, 10)
student = torch.compile(student.to(device))

<ipython-input-20-de996186d8e5>:2: FutureWarning: You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbitrary code during unpickling (See https://github.com/pytorch/pytorch/blob/main/SECURITY.md#untrusted-models for more details). In a future release, the default value for `weights_only` will be flipped to `True`. This limits the functions that could be executed during unpickling. Arbitrary objects will no longer be allowed to be loaded via this mode unless they are explicitly allowlisted by the user via `torch.serialization.add_safe_globals`. We recommend you start setting `weights_only=True` for any use case where you don't have full control of the loaded file. Please open an issue on GitHub for any issues related to this experimental feature.
  teacher = torch.load("/content/resnet18_14_15_14.pt", map_location=device)


## Training

In [ ]:
# Login into wandb
wandb.login(key=WANDB_KEY)

# Define hyperparameters
config = dict(
    distillation_type="logits",
    distillation_factor=0.5,
    temperature=1,
    model_base="resnet18",
    n_layers=8,
    n_params=1.2e6,
    epochs=20,
    batch_size=batch_size,
    learning_rate=3e-4,
)

optimizer = torch.optim.Adam(student.parameters(), lr=config["learning_rate"])
loss_fn = nn.CrossEntropyLoss(reduction="sum")
metrics = Metrics(i2c, device)

wandb: WARNING If you're specifying your api key in code, ensure this code is not shared publicly.
wandb: WARNING Consider setting the WANDB_API_KEY environment variable, or running `wandb login` from the command line.
wandb: Appending key for api.wandb.ai to your netrc file: /root/.netrc


In [ ]:
student = logits_distillation_train(
    teacher,
    student,
    optimizer,
    loss_fn,
    trainloader,
    valloader,
    metrics,
    device,
    config,
    "images-hw3",
    Path("./models"),
)

Epochs:   0%|          | 0/20 [00:00<?, ?it/s]

Training:   0%|          | 0/88 [00:00<?, ?it/s]

Exception ignored in: <function _MultiProcessingDataLoaderIter.__del__ at 0x78623c2dd580>
Traceback (most recent call last):
  File "/usr/local/lib/python3.11/dist-packages/torch/utils/data/dataloader.py", line 1604, in __del__
    self._shutdown_workers()
  File "/usr/local/lib/python3.11/dist-packages/torch/utils/data/dataloader.py", line 1587, in _shutdown_workers
    if w.is_alive():
       ^^^^^^^^^^^^
  File "/usr/lib/python3.11/multiprocessing/process.py", line 160, in is_alive
    assert self._parent_pid == os.getpid(), 'can only test a child process'Exception ignored in: <function _MultiProcessingDataLoaderIter.__del__ at 0x78623c2dd580>

Traceback (most recent call last):
  File "/usr/local/lib/python3.11/dist-packages/torch/utils/data/dataloader.py", line 1604, in __del__
      self._shutdown_workers()
  File "/usr/local/lib/python3.11/dist-packages/torch/utils/data/dataloader.py", line 1587, in _shutdown_workers
         if w.is_alive():
         ^ ^^^ ^^^^^^^^^^^^^^^^^^^^^

Validation:   0%|          | 0/10 [00:00<?, ?it/s]

Exception ignored in: <function _MultiProcessingDataLoaderIter.__del__ at 0x78623c2dd580>
Traceback (most recent call last):
  File "/usr/local/lib/python3.11/dist-packages/torch/utils/data/dataloader.py", line 1604, in __del__
    self._shutdown_workers()
  File "/usr/local/lib/python3.11/dist-packages/torch/utils/data/dataloader.py", line 1587, in _shutdown_workers
    if w.is_alive():
       ^^^^^^^^^^^^
  File "/usr/lib/python3.11/multiprocessing/process.py", line 160, in is_alive
Exception ignored in:     <function _MultiProcessingDataLoaderIter.__del__ at 0x78623c2dd580>
assert self._parent_pid == os.getpid(), 'can only test a child process'Traceback (most recent call last):

  File "/usr/local/lib/python3.11/dist-packages/torch/utils/data/dataloader.py", line 1604, in __del__
     self._shutdown_workers()
   File "/usr/local/lib/python3.11/dist-packages/torch/utils/data/dataloader.py", line 1587, in _shutdown_workers
      if w.is_alive(): 
   Exception ignored in:  <function _M

...

Validation:   0%|          | 0/10 [00:00<?, ?it/s]

Exception ignored in: <function _MultiProcessingDataLoaderIter.__del__ at 0x78623c2dd580>
Traceback (most recent call last):
  File "/usr/local/lib/python3.11/dist-packages/torch/utils/data/dataloader.py", line 1604, in __del__
    self._shutdown_workers()
Exception ignored in:   File "/usr/local/lib/python3.11/dist-packages/torch/utils/data/dataloader.py", line 1587, in _shutdown_workers
<function _MultiProcessingDataLoaderIter.__del__ at 0x78623c2dd580>    
if w.is_alive():Traceback (most recent call last):

  File "/usr/local/lib/python3.11/dist-packages/torch/utils/data/dataloader.py", line 1604, in __del__
      self._shutdown_workers() 
  File "/usr/local/lib/python3.11/dist-packages/torch/utils/data/dataloader.py", line 1587, in _shutdown_workers
Exception ignored in:      <function _MultiProcessingDataLoaderIter.__del__ at 0x78623c2dd580> 
if w.is_alive(): Traceback (most recent call last):

  File "/usr/local/lib/python3.11/dist-packages/torch/utils/data/dataloader.py", line 1

Training:   0%|          | 0/88 [00:00<?, ?it/s]

Validation:   0%|          | 0/10 [00:00<?, ?it/s]

Exception ignored in: <function _MultiProcessingDataLoaderIter.__del__ at 0x78623c2dd580>
Traceback (most recent call last):
  File "/usr/local/lib/python3.11/dist-packages/torch/utils/data/dataloader.py", line 1604, in __del__
    self._shutdown_workers()
  File "/usr/local/lib/python3.11/dist-packages/torch/utils/data/dataloader.py", line 1587, in _shutdown_workers
    if w.is_alive():
       ^^^^^^^^^^^^
  File "/usr/lib/python3.11/multiprocessing/process.py", line 160, in is_alive
    assert self._parent_pid == os.getpid(), 'can only test a child process'
           ^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^
AssertionError: can only test a child process


## Testing

In [ ]:
student = torch.load("/content/models/logits_0.5_1_resnet18_8_20_14.pt", map_location=device)  # Load best model
test(student, testloader, metrics, device, config, "images-hw3")

<ipython-input-24-640f5b530aba>:1: FutureWarning: You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbitrary code during unpickling (See https://github.com/pytorch/pytorch/blob/main/SECURITY.md#untrusted-models for more details). In a future release, the default value for `weights_only` will be flipped to `True`. This limits the functions that could be executed during unpickling. Arbitrary objects will no longer be allowed to be loaded via this mode unless they are explicitly allowlisted by the user via `torch.serialization.add_safe_globals`. We recommend you start setting `weights_only=True` for any use case where you don't have full control of the loaded file. Please open an issue on GitHub for any issues related to this experimental feature.
  student = torch.load("/content/models/logits_0.5_1_resnet18_8_20_14.pt", map_location=device

Test:   0%|          | 0/20 [00:00<?, ?it/s]

Exception ignored in: <function _MultiProcessingDataLoaderIter.__del__ at 0x78623c2dd580>
Traceback (most recent call last):
  File "/usr/local/lib/python3.11/dist-packages/torch/utils/data/dataloader.py", line 1604, in __del__
    self._shutdown_workers()
  File "/usr/local/lib/python3.11/dist-packages/torch/utils/data/dataloader.py", line 1587, in _shutdown_workers
    if w.is_alive():
       ^^^^^^^^^^^^
Exception ignored in:   File "/usr/lib/python3.11/multiprocessing/process.py", line 160, in is_alive
<function _MultiProcessingDataLoaderIter.__del__ at 0x78623c2dd580>    assert self._parent_pid == os.getpid(), 'can only test a child process'

Traceback (most recent call last):
   File "/usr/local/lib/python3.11/dist-packages/torch/utils/data/dataloader.py", line 1604, in __del__
      self._shutdown_workers() 
   File "/usr/local/lib/python3.11/dist-packages/torch/utils/data/dataloader.py", line 1587, in _shutdown_workers
      if w.is_alive(): 
 Exception ignored in:   <function 

# Experiment 2: untrained hidden layer distillation

## Load models

In [ ]:
# Load and prune pretrained teacher model
teacher = torch.load("/content/resnet18_14_15_14.pt", map_location=device)
teacher.layer3 = Identity()
teacher.avgpool = Identity()
teacher.fc = Identity()
teacher = torch.compile(teacher)

In [36]:
# Change the forward function of student model
# To get the needed output of hidden layer
def modified_forward(self, x):
        x = self.conv1(x)
        x = self.bn1(x)
        x = self.relu(x)
        x = self.layer1(x)
        distill_feature_map = self.layer2(x)
        x = self.layer3(distill_feature_map)
        x = self.avgpool(x)
        x = torch.flatten(x, 1)
        x = self.fc(x)

        return x, self.layer4(distill_feature_map)

torchvision.models.ResNet.forward.__code__ = modified_forward.__code__

In [37]:
# Set up student model
student = resnet18()
student.conv1 = nn.Conv2d(3, 64, kernel_size=3, stride=1, padding=1, bias=False)
student.maxpool = Identity()
student.layer1[1] = Identity()
student.layer2[1] = Identity()
student.layer3[1] = Identity()
student.fc = nn.Linear(256, 10)
# We would treat `layer4` as module of transforming the feature map from student
# before we use it in distillation
student.layer4 = torch.nn.Flatten(1)

student = torch.compile(student.to(device))

## Training

In [38]:
# Login into wandb
wandb.login(key=WANDB_KEY)

# Define hyperparameters
config = dict(
    distillation_type="untrained_hidden",
    distillation_factor=0.5,
    model_base="resnet18",
    n_layers=8,
    n_params=1.2e6,
    epochs=20,
    batch_size=batch_size,
    learning_rate=3e-4,
)

optimizer = torch.optim.Adam(student.parameters(), lr=config["learning_rate"])
loss_fn = nn.CrossEntropyLoss(reduction="mean")
metrics = Metrics(i2c, device)

wandb: WARNING If you're specifying your api key in code, ensure this code is not shared publicly.
wandb: WARNING Consider setting the WANDB_API_KEY environment variable, or running `wandb login` from the command line.
wandb: Appending key for api.wandb.ai to your netrc file: /root/.netrc


In [39]:
student = untrained_hidden_layer_distillation_train(
    teacher,
    student,
    optimizer,
    loss_fn,
    trainloader,
    valloader,
    metrics,
    device,
    config,
    "images-hw3",
    Path("./models"),
)

Epochs:   0%|          | 0/20 [00:00<?, ?it/s]

Training:   0%|          | 0/88 [00:00<?, ?it/s]

Validation:   0%|          | 0/10 [00:00<?, ?it/s]

Training:   0%|          | 0/88 [00:00<?, ?it/s]

Validation:   0%|          | 0/10 [00:00<?, ?it/s]

...

Validation:   0%|          | 0/10 [00:00<?, ?it/s]

Exception ignored in: <function _MultiProcessingDataLoaderIter.__del__ at 0x7d644c359620>
Traceback (most recent call last):
  File "/usr/local/lib/python3.11/dist-packages/torch/utils/data/dataloader.py", line 1604, in __del__
    self._shutdown_workers()
  File "/usr/local/lib/python3.11/dist-packages/torch/utils/data/dataloader.py", line 1587, in _shutdown_workers
    Exception ignored in: if w.is_alive():<function _MultiProcessingDataLoaderIter.__del__ at 0x7d644c359620>
       ^^^
^Traceback (most recent call last):
Exception ignored in: <function _MultiProcessingDataLoaderIter.__del__ at 0x7d644c359620>  File "/usr/local/lib/python3.11/dist-packages/torch/utils/data/dataloader.py", line 1604, in __del__
^
    self._shutdown_workers()^Traceback (most recent call last):
^Exception ignored in:   File "/usr/local/lib/python3.11/dist-packages/torch/utils/data/dataloader.py", line 1604, in __del__
^
    <function _MultiProcessingDataLoaderIter.__del__ at 0x7d644c359620>  File "/usr/loc

Training:   0%|          | 0/88 [00:00<?, ?it/s]

^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^
^^^  File "/usr/lib/python3.11/multiprocessing/process.py", line 160, in is_alive
^^^    ^^assert self._parent_pid == os.getpid(), 'can only test a child process'^
^^AssertionError
^
 : ^AssertionError can only test a child process^:  
^can only test a child process ^
 ^Exception ignored in:  ^Exception ignored in:  <function _MultiProcessingDataLoaderIter.__del__ at 0x7d644c359620>
<function _MultiProcessingDataLoaderIter.__del__ at 0x7d644c359620> 
AssertionError
Traceback (most recent call last):
 : Traceback (most recent call last):
   File "/usr/local/lib/python3.11/dist-packages/torch/utils/data/dataloader.py", line 1604, in __del__
can only test a child process  File "/usr/local/lib/python3.11/dist-packages/torch/utils/data/dataloader.py", line 1604, in __del__
         
self._shutdown_workers()^^self._shutdown_workers()
^^Exception ignored in:   File "/usr/local/lib/python3.11/dist-packages/torch/utils/data/dataloader.py", line 1587, in

Validation:   0%|          | 0/10 [00:00<?, ?it/s]

## Testing

In [41]:
student = torch.load("/content/models/untrained_hidden_0.5_resnet18_8_20_12.pt", map_location=device)  # Load best model
test(student, testloader, metrics, device, config, "images-hw3")

<ipython-input-41-54d465ecb0bf>:1: FutureWarning: You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbitrary code during unpickling (See https://github.com/pytorch/pytorch/blob/main/SECURITY.md#untrusted-models for more details). In a future release, the default value for `weights_only` will be flipped to `True`. This limits the functions that could be executed during unpickling. Arbitrary objects will no longer be allowed to be loaded via this mode unless they are explicitly allowlisted by the user via `torch.serialization.add_safe_globals`. We recommend you start setting `weights_only=True` for any use case where you don't have full control of the loaded file. Please open an issue on GitHub for any issues related to this experimental feature.
  student = torch.load("/content/models/untrained_hidden_0.5_resnet18_8_20_12.pt", map_locatio

Test:   0%|          | 0/20 [00:00<?, ?it/s]

Exception ignored in: <function _MultiProcessingDataLoaderIter.__del__ at 0x7d644c359620>
Traceback (most recent call last):
Exception ignored in:   File "/usr/local/lib/python3.11/dist-packages/torch/utils/data/dataloader.py", line 1604, in __del__
<function _MultiProcessingDataLoaderIter.__del__ at 0x7d644c359620>    
self._shutdown_workers()Traceback (most recent call last):

  File "/usr/local/lib/python3.11/dist-packages/torch/utils/data/dataloader.py", line 1604, in __del__
  File "/usr/local/lib/python3.11/dist-packages/torch/utils/data/dataloader.py", line 1587, in _shutdown_workers
    if w.is_alive():    
self._shutdown_workers() 
   File "/usr/local/lib/python3.11/dist-packages/torch/utils/data/dataloader.py", line 1587, in _shutdown_workers
      if w.is_alive(): 
   ^ ^ ^ ^ ^Exception ignored in:  ^<function _MultiProcessingDataLoaderIter.__del__ at 0x7d644c359620>
 ^^^Traceback (most recent call last):
^^  File "/usr/local/lib/python3.11/dist-packages/torch/utils/data/dat

# Experiment 3: trained hidden layer distillation

## Load models

In [15]:
# Load and prune pretrained teacher model
teacher = torch.load("/content/resnet18_14_15_14.pt", map_location=device)
teacher.layer3 = Identity()
teacher.avgpool = Identity()
teacher.fc = Identity()
teacher = torch.compile(teacher)

<ipython-input-15-2b67dac64620>:2: FutureWarning: You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbitrary code during unpickling (See https://github.com/pytorch/pytorch/blob/main/SECURITY.md#untrusted-models for more details). In a future release, the default value for `weights_only` will be flipped to `True`. This limits the functions that could be executed during unpickling. Arbitrary objects will no longer be allowed to be loaded via this mode unless they are explicitly allowlisted by the user via `torch.serialization.add_safe_globals`. We recommend you start setting `weights_only=True` for any use case where you don't have full control of the loaded file. Please open an issue on GitHub for any issues related to this experimental feature.
  teacher = torch.load("/content/resnet18_14_15_14.pt", map_location=device)


In [16]:
# Change the forward function of student model
# To get the needed output of hidden layer
def modified_forward(self, x):
        x = self.conv1(x)
        x = self.bn1(x)
        x = self.relu(x)
        x = self.layer1(x)
        distill_feature_map = self.layer2(x)
        x = self.layer3(distill_feature_map)
        x = self.avgpool(x)
        x = torch.flatten(x, 1)
        x = self.fc(x)

        return x, self.layer4(distill_feature_map)

torchvision.models.ResNet.forward.__code__ = modified_forward.__code__

In [17]:
# Set up student model
student = resnet18()
student.conv1 = nn.Conv2d(3, 64, kernel_size=3, stride=1, padding=1, bias=False)
student.maxpool = Identity()
student.layer1[1] = Identity()
student.layer2[1] = Identity()
student.layer3[1] = Identity()
student.fc = nn.Linear(256, 10)
# We would treat `layer4` as module of transforming the feature map from student
# before we use it in distillation
student.layer4 = torch.nn.Sequential(
    torch.nn.Conv2d(128, 128, 3, 1, 1),
    torch.nn.Flatten(1)
)

student = torch.compile(student.to(device))

## Training

In [18]:
# Login into wandb
wandb.login(key=WANDB_KEY)

# Define hyperparameters
config = dict(
    distillation_type="trained_hidden",
    distillation_factor=0.5,
    model_base="resnet18",
    n_layers=8,
    n_params=1.2e6,
    epochs=20,
    batch_size=batch_size,
    learning_rate=3e-4,
)

optimizer = torch.optim.Adam(student.parameters(), lr=config["learning_rate"])
loss_fn = nn.CrossEntropyLoss(reduction="mean")
metrics = Metrics(i2c, device)

wandb: Currently logged in as: deniskirbaba (deniskirbaba-team). Use `wandb login --relogin` to force relogin
wandb: WARNING If you're specifying your api key in code, ensure this code is not shared publicly.
wandb: WARNING Consider setting the WANDB_API_KEY environment variable, or running `wandb login` from the command line.
wandb: Appending key for api.wandb.ai to your netrc file: /root/.netrc


In [19]:
student = untrained_hidden_layer_distillation_train(
    teacher,
    student,
    optimizer,
    loss_fn,
    trainloader,
    valloader,
    metrics,
    device,
    config,
    "images-hw3",
    Path("./models"),
)

wandb: Using wandb-core as the SDK backend.  Please refer to https://wandb.me/wandb-core for more information.


Epochs:   0%|          | 0/20 [00:00<?, ?it/s]

Training:   0%|          | 0/88 [00:00<?, ?it/s]

Validation:   0%|          | 0/10 [00:00<?, ?it/s]

Training:   0%|          | 0/88 [00:00<?, ?it/s]

...

Validation:   0%|          | 0/10 [00:00<?, ?it/s]

Training:   0%|          | 0/88 [00:00<?, ?it/s]

Exception ignored in: <function _MultiProcessingDataLoaderIter.__del__ at 0x79d4b5151f80>
Traceback (most recent call last):
  File "/usr/local/lib/python3.11/dist-packages/torch/utils/data/dataloader.py", line 1604, in __del__
    self._shutdown_workers()
  File "/usr/local/lib/python3.11/dist-packages/torch/utils/data/dataloader.py", line 1587, in _shutdown_workers
    if w.is_alive():
       ^^^^^^^^^^^^
  File "/usr/lib/python3.11/multiprocessing/process.py", line 160, in is_alive
    assert self._parent_pid == os.getpid(), 'can only test a child process'
 Exception ignored in:  <function _MultiProcessingDataLoaderIter.__del__ at 0x79d4b5151f80> 
 Traceback (most recent call last):
  File "/usr/local/lib/python3.11/dist-packages/torch/utils/data/dataloader.py", line 1604, in __del__
       self._shutdown_workers() 
   File "/usr/local/lib/python3.11/dist-packages/torch/utils/data/dataloader.py", line 1587, in _shutdown_workers
      if w.is_alive():^^^
^^  ^ ^ ^ ^ ^ ^^^^^^^^^^^^^^^

Validation:   0%|          | 0/10 [00:00<?, ?it/s]

Exception ignored in: <function _MultiProcessingDataLoaderIter.__del__ at 0x79d4b5151f80>
Traceback (most recent call last):
  File "/usr/local/lib/python3.11/dist-packages/torch/utils/data/dataloader.py", line 1604, in __del__
    self._shutdown_workers()
  File "/usr/local/lib/python3.11/dist-packages/torch/utils/data/dataloader.py", line 1587, in _shutdown_workers
    if w.is_alive():
       ^^^^^^^^^^^^
  File "/usr/lib/python3.11/multiprocessing/process.py", line 160, in is_alive
    assert self._parent_pid == os.getpid(), 'can only test a child process'
           ^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^
AssertionError: can only test a child process
Exception ignored in: <function _MultiProcessingDataLoaderIter.__del__ at 0x79d4b5151f80>
Traceback (most recent call last):
  File "/usr/local/lib/python3.11/dist-packages/torch/utils/data/dataloader.py", line 1604, in __del__
    self._shutdown_workers()
  File "/usr/local/lib/python3.11/dist-packages/torch/utils/data/dataloader.py", line 15

## Testing

In [21]:
student = torch.load("/content/models/trained_hidden_0.5_resnet18_8_20_15.pt", map_location=device)  # Load best model
test(student, testloader, metrics, device, config, "images-hw3")

<ipython-input-21-0eed212d58d9>:1: FutureWarning: You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbitrary code during unpickling (See https://github.com/pytorch/pytorch/blob/main/SECURITY.md#untrusted-models for more details). In a future release, the default value for `weights_only` will be flipped to `True`. This limits the functions that could be executed during unpickling. Arbitrary objects will no longer be allowed to be loaded via this mode unless they are explicitly allowlisted by the user via `torch.serialization.add_safe_globals`. We recommend you start setting `weights_only=True` for any use case where you don't have full control of the loaded file. Please open an issue on GitHub for any issues related to this experimental feature.
  student = torch.load("/content/models/trained_hidden_0.5_resnet18_8_20_15.pt", map_location=

Test:   0%|          | 0/20 [00:00<?, ?it/s]

# Experiment 4: logits + trained hidden layer distillation

## Load models

In [40]:
# Load and edit pretrained teacher model
teacher = torch.load("/content/resnet18_14_15_14.pt", map_location=device)
teacher.layer4 = torch.nn.Flatten(1)
teacher = torch.compile(teacher)

<ipython-input-40-ad5faf7e0837>:2: FutureWarning: You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbitrary code during unpickling (See https://github.com/pytorch/pytorch/blob/main/SECURITY.md#untrusted-models for more details). In a future release, the default value for `weights_only` will be flipped to `True`. This limits the functions that could be executed during unpickling. Arbitrary objects will no longer be allowed to be loaded via this mode unless they are explicitly allowlisted by the user via `torch.serialization.add_safe_globals`. We recommend you start setting `weights_only=True` for any use case where you don't have full control of the loaded file. Please open an issue on GitHub for any issues related to this experimental feature.
  teacher = torch.load("/content/resnet18_14_15_14.pt", map_location=device)


In [25]:
# Change the forward function of student model
# To get the needed output of hidden layer
def modified_forward(self, x):
        x = self.conv1(x)
        x = self.bn1(x)
        x = self.relu(x)
        x = self.layer1(x)
        distill_feature_map = self.layer2(x)
        x = self.layer3(distill_feature_map)
        x = self.avgpool(x)
        x = torch.flatten(x, 1)
        x = self.fc(x)

        return x, self.layer4(distill_feature_map)

torchvision.models.ResNet.forward.__code__ = modified_forward.__code__

In [26]:
# Set up student model
student = resnet18()
student.conv1 = nn.Conv2d(3, 64, kernel_size=3, stride=1, padding=1, bias=False)
student.maxpool = Identity()
student.layer1[1] = Identity()
student.layer2[1] = Identity()
student.layer3[1] = Identity()
student.fc = nn.Linear(256, 10)
# We would treat `layer4` as module of transforming the feature map from student
# before we use it in distillation
student.layer4 = torch.nn.Sequential(
    torch.nn.Conv2d(128, 128, 3, 1, 1),
    torch.nn.Flatten(1)
)

student = torch.compile(student.to(device))

## Training

In [35]:
# Login into wandb
wandb.login(key=WANDB_KEY)

# Define hyperparameters
config = dict(
    distillation_type="hybrid",
    logits_dist_factor=1.0,
    temperature=1.0,
    hidden_trained_dist_factor=1.0,
    model_base="resnet18",
    n_layers=8,
    n_params=1.2e6,
    epochs=20,
    batch_size=batch_size,
    learning_rate=3e-4,
)

optimizer = torch.optim.Adam(student.parameters(), lr=config["learning_rate"])
loss_fn = nn.CrossEntropyLoss(reduction="mean")
metrics = Metrics(i2c, device)

wandb: WARNING If you're specifying your api key in code, ensure this code is not shared publicly.
wandb: WARNING Consider setting the WANDB_API_KEY environment variable, or running `wandb login` from the command line.
wandb: Appending key for api.wandb.ai to your netrc file: /root/.netrc


In [42]:
student = hybrid_distillation_train(
    teacher,
    student,
    optimizer,
    loss_fn,
    trainloader,
    valloader,
    metrics,
    device,
    config,
    "images-hw3",
    Path("./models"),
)

Epochs:   0%|          | 0/20 [00:00<?, ?it/s]

Training:   0%|          | 0/88 [00:00<?, ?it/s]

W0123 17:51:32.279000 724 torch/_dynamo/convert_frame.py:844] [3/8] torch._dynamo hit config.cache_size_limit (8)
W0123 17:51:32.279000 724 torch/_dynamo/convert_frame.py:844] [3/8]    function: 'forward' (/usr/local/lib/python3.11/dist-packages/torchvision/models/resnet.py:89)
W0123 17:51:32.279000 724 torch/_dynamo/convert_frame.py:844] [3/8]    last reason: 3/0: GLOBAL_STATE changed: grad_mode 
W0123 17:51:32.279000 724 torch/_dynamo/convert_frame.py:844] [3/8] To log all recompilation reasons, use TORCH_LOGS="recompiles".
W0123 17:51:32.279000 724 torch/_dynamo/convert_frame.py:844] [3/8] To diagnose recompilation issues, see https://pytorch.org/docs/main/torch.compiler_troubleshooting.html.


Validation:   0%|          | 0/10 [00:00<?, ?it/s]

Training:   0%|          | 0/88 [00:00<?, ?it/s]

...

Validation:   0%|          | 0/10 [00:00<?, ?it/s]

Exception ignored in: <function _MultiProcessingDataLoaderIter.__del__ at 0x79d4b5151f80>
Traceback (most recent call last):
  File "/usr/local/lib/python3.11/dist-packages/torch/utils/data/dataloader.py", line 1604, in __del__
Exception ignored in:     self._shutdown_workers()<function _MultiProcessingDataLoaderIter.__del__ at 0x79d4b5151f80>
  File "/usr/local/lib/python3.11/dist-packages/torch/utils/data/dataloader.py", line 1587, in _shutdown_workers

    Traceback (most recent call last):
  File "/usr/local/lib/python3.11/dist-packages/torch/utils/data/dataloader.py", line 1604, in __del__
if w.is_alive():    
self._shutdown_workers() 
  File "/usr/local/lib/python3.11/dist-packages/torch/utils/data/dataloader.py", line 1587, in _shutdown_workers
       if w.is_alive():
     ^ ^ ^^  ^ ^^^^^^^^^^^^^^^
^  File "/usr/lib/python3.11/multiprocessing/process.py", line 160, in is_alive
^    ^assert self._parent_pid == os.getpid(), 'can only test a child process'^

Exception ignored in: E

Training:   0%|          | 0/88 [00:00<?, ?it/s]

Exception ignored in: <function _MultiProcessingDataLoaderIter.__del__ at 0x79d4b5151f80>
Traceback (most recent call last):
  File "/usr/local/lib/python3.11/dist-packages/torch/utils/data/dataloader.py", line 1604, in __del__
    self._shutdown_workers()
  File "/usr/local/lib/python3.11/dist-packages/torch/utils/data/dataloader.py", line 1587, in _shutdown_workers
    if w.is_alive():
Exception ignored in:   <function _MultiProcessingDataLoaderIter.__del__ at 0x79d4b5151f80>
 Traceback (most recent call last):
    File "/usr/local/lib/python3.11/dist-packages/torch/utils/data/dataloader.py", line 1604, in __del__
     self._shutdown_workers() 
^  File "/usr/local/lib/python3.11/dist-packages/torch/utils/data/dataloader.py", line 1587, in _shutdown_workers
^^    Exception ignored in: if w.is_alive():^<function _MultiProcessingDataLoaderIter.__del__ at 0x79d4b5151f80>

^ ^Traceback (most recent call last):
 ^  File "/usr/local/lib/python3.11/dist-packages/torch/utils/data/dataloader.p

Validation:   0%|          | 0/10 [00:00<?, ?it/s]

## Testing

In [44]:
student = torch.load("/content/models/hybrid_1.0_1.0_resnet18_8_20_13.pt", map_location=device)  # Load best model
test(student, testloader, metrics, device, config, "images-hw3")

<ipython-input-44-e38af0f3ea36>:1: FutureWarning: You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbitrary code during unpickling (See https://github.com/pytorch/pytorch/blob/main/SECURITY.md#untrusted-models for more details). In a future release, the default value for `weights_only` will be flipped to `True`. This limits the functions that could be executed during unpickling. Arbitrary objects will no longer be allowed to be loaded via this mode unless they are explicitly allowlisted by the user via `torch.serialization.add_safe_globals`. We recommend you start setting `weights_only=True` for any use case where you don't have full control of the loaded file. Please open an issue on GitHub for any issues related to this experimental feature.
  student = torch.load("/content/models/hybrid_1.0_1.0_resnet18_8_20_13.pt", map_location=devi

Test:   0%|          | 0/20 [00:00<?, ?it/s]